In [1]:
import pandas as pd
import pandas as pd
import numpy as np
from sklearn.manifold import TSNE
import plotly.express as px

In [75]:
!mkdir ../data

mkdir: ../data: File exists


Download dataset and paste zip in the ../data/ directory

unzip it

In [69]:
!unzip ../data/dataset_conll.zip -d ../data

Archive:  ../data/dataset_conll.zip
   creating: ../data/dataset_conll/
  inflating: ../data/dataset_conll/Nhotels.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nhotels.sentence.train.txt  
  inflating: ../data/dataset_conll/Nhotels.text.dev.txt  
  inflating: ../data/dataset_conll/Nhotels.text.train.txt  
  inflating: ../data/dataset_conll/Nmedicine.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nmedicine.sentence.train.txt  
  inflating: ../data/dataset_conll/Nmedicine.text.dev.txt  
  inflating: ../data/dataset_conll/Nmedicine.text.train.txt  
  inflating: ../data/dataset_conll/Nproducts.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nproducts.sentence.train.txt  
  inflating: ../data/dataset_conll/Nproducts.text.dev.txt  
  inflating: ../data/dataset_conll/Nproducts.text.train.txt  
  inflating: ../data/dataset_conll/Nreviews.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nreviews.sentence.train.txt  
  inflating: ../data/dataset_conll/Nreviews.text.dev

In [2]:
import os

# Define the path to the dataset directory
dataset_dir = os.path.join('..','data', 'dataset_conll')

# Function to read FastText formatted files
def read_fasttext_files(directory, filename_prefix):
    data = []
    for filename in os.listdir(directory):
        if filename.startswith(filename_prefix) and filename.endswith('.txt'):
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r', encoding='utf-8') as file:
                for line in file:
                    data.append(line.strip())
    return data

# Read the dataset
train = read_fasttext_files(dataset_dir, 'products.text.train')
test = read_fasttext_files(dataset_dir, 'products.text.test')
dev = read_fasttext_files(dataset_dir, 'products.text.dev')
#show how many lines are in the file
print(len(train))
print(len(test))
print(len(dev))

387
48
49


In [3]:
from collections import defaultdict

def group_files_by_topic(directory):
    topic_counts = defaultdict(int)
    
    for filename in os.listdir(directory):
        if filename.endswith('.txt'):
            topic = '.'.join(filename.split('.')[:2])
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r', encoding='utf-8') as file:
                line_count = sum(1 for _ in file)
                topic_counts[topic] += line_count
    
    return topic_counts

# Group files by topic and count lines
topic_counts = group_files_by_topic(dataset_dir)

# Display the results
for topic, count in topic_counts.items():
    print(f"Topic: {topic}, Lines: {count}")

Topic: products.text, Lines: 484
Topic: all.text, Lines: 8216
Topic: Nreviews.text, Lines: 6942
Topic: products.sentence, Lines: 7427
Topic: Nreviews.sentence, Lines: 49443
Topic: hotels.sentence, Lines: 24851
Topic: medicine.sentence, Lines: 22657
Topic: medicine.text, Lines: 3272
Topic: Nproducts.text, Lines: 6960
Topic: all.sentence, Lines: 57466
Topic: reviews.text, Lines: 504
Topic: Nhotels.text, Lines: 3835
Topic: reviews.sentence, Lines: 2531
Topic: hotels.text, Lines: 3956
Topic: Nmedicine.sentence, Lines: 31329
Topic: Nmedicine.text, Lines: 4451
Topic: Nhotels.sentence, Lines: 29355
Topic: Nproducts.sentence, Lines: 45036


Oddzielenie zdania od annotacji

In [4]:
reviews_text_train = read_fasttext_files(dataset_dir, 'products.sentence.train')
reviews_text_test = read_fasttext_files(dataset_dir, 'products.sentence.test')
reviews_text_dev = read_fasttext_files(dataset_dir, 'products.sentence.dev')

def parse_fasttext_data(data):
    parsed_data = []
    for line in data:
        if '__label__' in line:
            parts = line.rsplit(' ', 1)
            text = parts[0]
            label = parts[1]
            parsed_data.append({'text': text, 'label': label})
    return pd.DataFrame(parsed_data)

# Parse the data into dataframes
train_df = parse_fasttext_data(reviews_text_train)
test_df = parse_fasttext_data(reviews_text_test)
dev_df = parse_fasttext_data(reviews_text_dev)

# Display the first few rows of the train dataframe
print(train_df.head())
train_df.describe()


                                                text              label
0                             Sklep OLEOLE rowniez .     __label__z_amb
1  Spędził em jako chłopiec przy tej grze wiele g...  __label__z_plus_m
2  To mój drugi elektryczny podgrzewacz wody , po...    __label__z_zero
3  Polecam wszystkim , którzy nie mogą mieć ładne...  __label__z_plus_m
4      i to w słonej wodzie na znacznej głębokości .  __label__z_plus_m


text               label
count                     5942                5942
unique                    5942                   4
top     Sklep OLEOLE rowniez .  __label__z_minus_m
freq                         1                2745

Krok preprocesingu

In [4]:
!pip install  nltk

In [5]:
import nltk
from nltk.corpus import stopwords
import string

nltk.download()
nltk.download("punkt_tab")

showing info https://raw.githubusercontent.com/nltk/nltk_data/gh-pages/index.xml


[nltk_data] Error loading punkt_tab: <urlopen error [SSL:
[nltk_data]     CERTIFICATE_VERIFY_FAILED] certificate verify failed:
[nltk_data]     unable to get local issuer certificate (_ssl.c:1000)>


False

download polish stopwords from: https://github.com/bieli/stopwords/blob/master/polish.stopwords.txt

In [6]:
# Define the path to the stopwords file
stopwords_file_path = os.path.join('..', 'data', 'polish.stopwords.txt')

# Function to load stopwords from a file
def load_stopwords(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        stopwords_list = [line.strip() for line in file]
    return set(stopwords_list)

# Load stopwords
custom_stopwords = load_stopwords(stopwords_file_path)

print(list(custom_stopwords)[:10])

['im', 'wtedy', 'tu', 'nad', 'wasze', 'jakoś', 'nich', 'inne', 'dokad', 'byc']


In [7]:
def preprocess_texts(text):
    # remove extra whitespace
    text = text.strip()
    text = " ".join(text.split())

    # tokenize text
    tokens = nltk.word_tokenize(text)

    # lowercase tokens
    tokens = [token.lower() for token in tokens]

    # remove punctuation
    tokens = [token for token in tokens if token not in string.punctuation]

    # remove stopwords
    tokens = [token for token in tokens if token.lower() not in custom_stopwords]
    return " ".join(tokens)

In [8]:
train_df['cleaned_text'] = train_df['text'].apply(preprocess_texts)
train_df.head()

text              label  \
0                             Sklep OLEOLE rowniez .     __label__z_amb   
1  Spędził em jako chłopiec przy tej grze wiele g...  __label__z_plus_m   
2  To mój drugi elektryczny podgrzewacz wody , po...    __label__z_zero   
3  Polecam wszystkim , którzy nie mogą mieć ładne...  __label__z_plus_m   
4      i to w słonej wodzie na znacznej głębokości .  __label__z_plus_m   

                                        cleaned_text  
0                                       sklep oleole  
1  spędził em chłopiec grze godzin muszę przyznać...  
2  drugi elektryczny podgrzewacz wody poprzedni d...  
3  polecam mieć ładnego metalowego eleganckiego t...  
4                  słonej wodzie znacznej głębokości

In [76]:
!mkdir ../models

mkdir: ../models: File exists


download model .gz and paste it in the ../models/ directory

Unpack model

In [10]:
!gunzip ../models/cc.pl.300.bin.gz -d ../models/

In [9]:
import fasttext

ft = fasttext.load_model('../models/cc.pl.300.bin')


In [13]:
!pip install plotly scikit-learn pandas

  Using cached plotly-5.24.1-py3-none-any.whl.metadata (7.3 kB)
  Using cached scikit_learn-1.5.2-cp312-cp312-macosx_12_0_arm64.whl.metadata (13 kB)
  Using cached pandas-2.2.3-cp312-cp312-macosx_11_0_arm64.whl.metadata (89 kB)
  Using cached tenacity-9.0.0-py3-none-any.whl.metadata (1.2 kB)
  Using cached scipy-1.14.1-cp312-cp312-macosx_14_0_arm64.whl.metadata (60 kB)
  Using cached joblib-1.4.2-py3-none-any.whl.metadata (5.4 kB)
  Using cached threadpoolctl-3.5.0-py3-none-any.whl.metadata (13 kB)
  Using cached pytz-2024.2-py2.py3-none-any.whl.metadata (22 kB)
  Using cached tzdata-2024.2-py2.py3-none-any.whl.metadata (1.4 kB)
Using cached plotly-5.24.1-py3-none-any.whl (19.1 MB)
Using cached scikit_learn-1.5.2-cp312-cp312-macosx_12_0_arm64.whl (11.0 MB)
Using cached pandas-2.2.3-cp312-cp312-macosx_11_0_arm64.whl (11.4 MB)
Using cached joblib-1.4.2-py3-none-any.whl (301 kB)
Using cached pytz-2024.2-py2.py3-none-any.whl (508 kB)
Using cached scipy-1.14.1-cp312-cp312-macosx_14_0_arm64.

# Word Embeddings

# Text Embeddings

## FastText

In [10]:
fasttext_df = train_df.copy()

fasttext_df["embeddings"] = fasttext_df["cleaned_text"].apply(  
    lambda x: ft.get_sentence_vector(x)
)

In [26]:
# Display the first few rows to verify
fasttext_df.head()

text              label  \
0                             Sklep OLEOLE rowniez .     __label__z_amb   
1  Spędził em jako chłopiec przy tej grze wiele g...  __label__z_plus_m   
2  To mój drugi elektryczny podgrzewacz wody , po...    __label__z_zero   
3  Polecam wszystkim , którzy nie mogą mieć ładne...  __label__z_plus_m   
4      i to w słonej wodzie na znacznej głębokości .  __label__z_plus_m   

                                        cleaned_text  \
0                                       sklep oleole   
1  spędził em chłopiec grze godzin muszę przyznać...   
2  drugi elektryczny podgrzewacz wody poprzedni d...   
3  polecam mieć ładnego metalowego eleganckiego t...   
4                  słonej wodzie znacznej głębokości   

                                          embeddings  cluster  
0  [0.073383, 0.038602598, -0.071955636, -0.00038...       -1  
1  [-0.0027373354, 0.00015096678, 0.012627825, 0....        2  
2  [0.034704305, -0.024992619, 0.021210141, -0.00...       -1  
3  [-0.0013542998, 0.030805156, 0.013557089, 0.04...        2  
4  [0.020909943, -0.0047461484, -0.025505979, -0....       -1

In [22]:
# Convert the list of embeddings into a 2D numpy array
embeddings_array_fasttext = np.array(fasttext_df["embeddings"].tolist())

In [27]:
tsne = TSNE(n_components=2, random_state=42, perplexity=30, max_iter=1000)
X_tsne = tsne.fit_transform(embeddings_array_fasttext)

fasttext_df["x-tsne"] = X_tsne[:, 0]
fasttext_df["y-tsne"] = X_tsne[:, 1]

In [28]:

# Create interactive scatter plot
fig = px.scatter(
    train_df, x='x-tsne', y='y-tsne', color='label',
    hover_data={'text': True, 'label': True},
    title='Sentences t-SNE Visualization with Fasttext Embeddings', width=1200, height=1200
)

# Show plot
fig.show()

## TF-IDF (sklearn)

In [17]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(max_features=300)
tfidf_df = train_df.copy()

X = vectorizer.fit_transform(tfidf_df["cleaned_text"])
print(f" Shape of the TF-IDF matrix: {X.shape}")

tfidf_df["embeddings"] = [X[i].toarray()[0] for i in range(X.shape[0])]

embeddings_array_tfidf = np.array(tfidf_df['embeddings'].tolist())


 Shape of the TF-IDF matrix: (5942, 300)


In [18]:

tsne_tfidf = TSNE(n_components=2, random_state=42, perplexity=30, max_iter=1000)
X_tsne_tfidf = tsne_tfidf.fit_transform(embeddings_array_tfidf)

# Add t-SNE results to the DataFrame
tfidf_df["x-tsne"] = X_tsne_tfidf[:, 0]
tfidf_df["y-tsne"] = X_tsne_tfidf[:, 1]

# Create interactive scatter plot
fig_tfidf = px.scatter(
    tfidf_df,
    x="x-tsne",
    y="y-tsne",
    color="label",
    hover_data={"cleaned_text": True, "label": True},
    title="Sentences t-SNE Visualization with TF-IDF Embeddings",
    width=1200,
    height=1200,
)
# Show plot

fig_tfidf.show()

## HDBSCAN (sklearn)

In [19]:
from sklearn.cluster import HDBSCAN
clusterer = HDBSCAN(
    min_cluster_size=5, metric="euclidean", cluster_selection_method="eom"
)

## FastText

In [29]:
fasttext_df["cluster"] = clusterer.fit_predict(embeddings_array_fasttext)

In [30]:
fasttext_df

text               label  \
0                                Sklep OLEOLE rowniez .      __label__z_amb   
1     Spędził em jako chłopiec przy tej grze wiele g...   __label__z_plus_m   
2     To mój drugi elektryczny podgrzewacz wody , po...     __label__z_zero   
3     Polecam wszystkim , którzy nie mogą mieć ładne...   __label__z_plus_m   
4         i to w słonej wodzie na znacznej głębokości .   __label__z_plus_m   
...                                                 ...                 ...   
5937  Kupił em trymer w grudniu 2016 r . , wytrzymał...  __label__z_minus_m   
5938  Zdecydowanie nie polecam i nie kupię grilla Ph...  __label__z_minus_m   
5939  Produkty mogę wrzucać w całości dzięki temu , ...   __label__z_plus_m   
5940  Daję mu 4 gwiazdki , bo gdyby m miała 20 lat m...      __label__z_amb   
5941  Nie wiem dlaczego ale często przy piciu córka ...  __label__z_minus_m   

                                           cleaned_text  \
0                                          sklep oleole   
1     spędził em chłopiec grze godzin muszę przyznać...   
2     drugi elektryczny podgrzewacz wody poprzedni d...   
3     polecam mieć ładnego metalowego eleganckiego t...   
4                     słonej wodzie znacznej głębokości   
...                                                 ...   
5937  kupił em trymer grudniu 2016 r wytrzymał wczor...   
5938  zdecydowanie polecam kupię grilla philipsa prz...   
5939  produkty mogę wrzucać całości dzięki temu posi...   
5940  daję 4 gwiazdki m miała 20 mniej pewnie m zado...   
5941                wiem często piciu córka zaksztusiła   

                                             embeddings  cluster     x-tsne  \
0     [0.073383, 0.038602598, -0.071955636, -0.00038...       -1  29.666630   
1     [-0.0027373354, 0.00015096678, 0.012627825, 0....        2   2.674295   
2     [0.034704305, -0.024992619, 0.021210141, -0.00...       -1  16.237535   
3     [-0.0013542998, 0.030805156, 0.013557089, 0.04...        2 -18.373798   
4     [0.020909943, -0.0047461484, -0.025505979, -0....       -1  13.195777   
...                                                 ...      ...        ...   
5937  [-0.016750902, 0.004048801, 0.01944663, -0.007...        2  12.130574   
5938  [-0.012293942, 0.010895947, 0.04530352, -0.001...        2 -11.481953   
5939  [-0.00981594, -0.0038990157, 0.035573337, 0.01...        2   4.622468   
5940  [0.019893644, 0.010456595, 0.02635831, -0.0039...        2   8.646783   
5941  [-0.02173839, 0.020793928, 0.040151563, -0.000...       -1  21.875824   

         y-tsne  
0      2.900178  
1      4.216548  
2    -33.036137  
3     12.418335  
4    -26.793486  
...         ...  
5937  37.999950  
5938  20.039633  
5939  -8.990636  
5940  37.010643  
5941  -8.067216  

[5942 rows x 7 columns]

In [31]:
fig_cluster = px.scatter(
    fasttext_df,
    x="x-tsne",
    y="y-tsne",
    color="cluster",
    hover_data={"cleaned_text": True, "label": True, "cluster": True},
    title="Sentences t-SNE Visualization with TF-IDF Embeddings and HDBSCAN Clustering",
    width=1200,
    height=1200,
)
fig_cluster.show()

## TF-IDF (sklearn)

In [32]:

tfidf_df['cluster'] = clusterer.fit_predict(embeddings_array_tfidf)


In [33]:
fig_cluster = px.scatter(
    tfidf_df,
    x="x-tsne",
    y="y-tsne",
    color="cluster",
    hover_data={"cleaned_text": True, "label": True, "cluster": True},
    title="Sentences t-SNE Visualization with TF-IDF Embeddings and HDBSCAN Clustering",
    width=1200,
    height=1200,
)

In [34]:
fig_cluster.show()
